In [1]:
from dotenv import load_dotenv

from core.data_sources.clob import CLOBDataSource
import warnings

from core.notifiers import NotificationManager, NotificationMessage

warnings.filterwarnings("ignore")

load_dotenv()

# Main class to access central limit order book connectors
clob = CLOBDataSource()

/opt/anaconda3/envs/quants-lab/lib/python3.12/site-packages/requests/__init__.py:86: RequestsDependencyWarning: Unable to find acceptable character detection dependency (chardet or charset_normalizer).
  warnings.warn(


In [2]:
# Configuration Parameters
CONFIG = {
    'connector_name': 'binance_perpetual',
    'interval': '1m',
    'ema_lengths': [20, 200, 500],
    'signal_intensity_threshold': 0.7,
    'min_range_pct': 0.01,
    'rolling_window': 1000,
}

# Load candles from cache
clob.load_candles_cache()
candles = []
for key, value in clob.candles_cache.items():
    if key[-1] == CONFIG['interval'] and key[0] == CONFIG['connector_name']:
        candles.append(value)

## Improved Feature Engineering System

Using the streamlined feature engineering system with:
- **One feature per strategy/calculation** (not per indicator)
- Flexible value types: float, List[float], or Dict[str, float]
- MongoDB-only storage for production use
- Standardized signal model with -1 to 1 scale
- Type-safe Pydantic models

In [3]:
# Import the new feature engineering system
from core.features import FeatureStorage, Feature, Signal
from core.features.candles.ema_trend import EMATrend, EMATrendConfig

# Initialize feature storage (MongoDB only)
storage = FeatureStorage()
await storage.connect()

In [4]:
# Initialize the EMA trend feature calculator
ema_config = EMATrendConfig(
    ema_lengths=CONFIG['ema_lengths'],
    rolling_window=CONFIG['rolling_window']
)

ema_trend = EMATrend(feature_config=ema_config)

print(f"✅ Initialized EMA Trend feature calculator")
print(f"   EMA lengths: {ema_config.ema_lengths}")
print(f"   Rolling window: {ema_config.rolling_window}")
print(f"\n📊 This creates ONE feature per pair containing all EMA trend data")

✅ Initialized EMA Trend feature calculator
   EMA lengths: [20, 200, 500]
   Rolling window: 1000

📊 This creates ONE feature per pair containing all EMA trend data


In [5]:
# Generate features and signals using the improved system
all_features = []
all_signals = []

signals_for_display = []

for candle in candles:
    try:
        # Pass the Candles object directly - much cleaner!
        feature = ema_trend.create_feature(candle)
        all_features.append(feature)
        
        # Create signal if criteria met
        signal = ema_trend.create_signal(
            candle,
            min_intensity=CONFIG['signal_intensity_threshold'],
            min_range_pct=CONFIG['min_range_pct']
        )
        
        if signal:
            all_signals.append(signal)
            
            # Collect for reporting (signal.value ranges from -1 to 1)
            signals_for_display.append({
                'trading_pair': signal.trading_pair,
                'category': signal.category,
                'signal_value': signal.value,
                'direction': 'LONG' if signal.value > 0 else 'SHORT',
                'intensity': abs(signal.value),
                'range_pct': feature.value['range_pct'],
                'ema_divergence': feature.value['divergence']
            })
                
    except Exception as e:
        print(f"Error processing {candle.trading_pair}: {e}")

print(f"\n✅ Processed {len(candles)} pairs")
print(f"📊 Generated {len(all_features)} features (1 per pair)")
print(f"🎯 Generated {len(all_signals)} signals")

Error processing ENSO-USDT: 'EMA_500'
Error processing CLO-USDT: 'EMA_500'

✅ Processed 519 pairs
📊 Generated 517 features (1 per pair)
🎯 Generated 73 signals


In [6]:
# Example: Show what a single feature looks like
if len(candles) > 0:
    example_candle = candles[0]
    
    # Now we just pass the Candles object - it contains everything!
    example_feature = ema_trend.create_feature(example_candle)
    
    print(f"📝 Example Feature for {example_feature.trading_pair}:")
    print(f"   Feature name: {example_feature.feature_name}")
    print(f"   Connector: {example_feature.connector_name}")
    print(f"   Timestamp: {example_feature.timestamp}")
    print(f"\n   Value (dict with all EMA trend data):")
    for key, val in example_feature.value.items():
        if isinstance(val, float):
            print(f"     • {key}: {val:.6f}")
        else:
            print(f"     • {key}: {val}")
    
    print(f"\n   Info (metadata):")
    for key, val in example_feature.info.items():
        print(f"     • {key}: {val}")

📝 Example Feature for PEOPLE-USDT:
   Feature name: ema_trend
   Connector: binance_perpetual
   Timestamp: 2025-10-14 16:56:50.099733+00:00

   Value (dict with all EMA trend data):
     • ema_20: 0.012884
     • ema_200: 0.012729
     • ema_500: 0.012759
     • direction: 1.000000
     • intensity: 0.609200
     • divergence: 0.000140
     • range_pct: 0.130805
     • price: 0.012920

   Info (metadata):
     • ema_lengths: [20, 200, 500]
     • rolling_window: 1000
     • description: EMA trend analysis using [20, 200, 500]
     • interval: 1m


### Visualize Feature

Features now have built-in visualization methods!

In [7]:
# Visualize the feature on candlestick chart
if len(candles) > 0:
    example_candle = candles[0]
    
    # The feature can plot itself!
    print(f"📈 Plotting {example_candle.trading_pair} with EMA Trend feature...")
    ema_trend.plot(example_candle, height=600, width=1400)

📈 Plotting PEOPLE-USDT with EMA Trend feature...


In [8]:
# Or manually add to an existing figure
if len(candles) > 0:
    example_candle = candles[0]
    
    # Start with candles
    fig = example_candle.candles_fig(height=600, width=1400)
    
    # Add the EMA trend feature
    fig = ema_trend.add_to_fig(fig, example_candle)
    
    # Could add more features here...
    # fig = another_feature.add_to_fig(fig, example_candle)
    
    fig.show()

In [9]:
# Save features and signals to MongoDB
print("Saving features and signals to MongoDB...")

# Save features
await storage.save_features(all_features)

# Save signals
await storage.save_signals(all_signals)

print(f"✅ Saved {len(all_features)} features")
print(f"✅ Saved {len(all_signals)} signals")

Saving features and signals to MongoDB...
✅ Saved 517 features
✅ Saved 73 signals


In [10]:
import pandas as pd

# Display signals in DataFrame format
signals_df = pd.DataFrame(signals_for_display).sort_values(by='intensity', ascending=False)

print(f"Total signals: {len(signals_df)}")
print(f"Long signals: {len(signals_df[signals_df['direction'] == 'LONG'])}")
print(f"Short signals: {len(signals_df[signals_df['direction'] == 'SHORT'])}")

# Show top signals
print("\\nTop 10 Signals:")
display(signals_df.head(10))

Total signals: 73
Long signals: 70
Short signals: 3
\nTop 10 Signals:


trading_pair category  signal_value direction  intensity  range_pct  \
8       SSV-USDT       tf        0.9644      LONG     0.9644 0.15035224   
17     TREE-USDT       tf        0.9428      LONG     0.9428 0.13396005   
68      TIA-USDT       tf        0.9334      LONG     0.9334 0.11537775   
31     OPEN-USDT       tf        0.9292      LONG     0.9292 0.17467356   
7      SCRT-USDT       tf        0.9248      LONG     0.9248 0.14651416   
18     ONDO-USDT       tf        0.9016      LONG     0.9016 0.12965374   
15     DOGE-USDT       tf        0.8992      LONG     0.8992  0.1125381   
21  MOODENG-USDT       tf        0.8975      LONG     0.8975  0.1233026   
60    AIXBT-USDT       tf         0.897      LONG      0.897 0.14303777   
25     AERO-USDT       tf        0.8962      LONG     0.8962 0.13128076   

    ema_divergence  
8       0.03250699  
17      0.00069809  
68      0.00778769  
31      0.00197063  
7       0.00098145  
18       0.0045296  
15      0.00064764  
21      0.00027747  
60      0.00037131  
25      0.00468533

### Summary Statistics

In [11]:
# Summary statistics
print("=" * 60)
print("FEATURE ENGINEERING SUMMARY")
print("=" * 60)

print(f"\n📊 Data Processing:")
print(f"   • Pairs processed: {len(candles)}")
print(f"   • Features generated: {len(all_features)} (1 per pair)")
print(f"   • Signals generated: {len(all_signals)}")

if len(signals_df) > 0:
    print(f"\n🎯 Signal Breakdown:")
    print(f"   • Long signals (value > 0): {len(signals_df[signals_df['direction'] == 'LONG'])}")
    print(f"   • Short signals (value < 0): {len(signals_df[signals_df['direction'] == 'SHORT'])}")
    print(f"   • Average intensity: {signals_df['intensity'].mean():.3f}")
    print(f"   • Max intensity: {signals_df['intensity'].max():.3f}")
    
print(f"\n💾 Storage:")
print(f"   • Features saved to MongoDB: {len(all_features)}")
print(f"   • Signals saved to MongoDB: {len(all_signals)}")
print(f"   • Collection: 'features' and 'signals'")

print(f"\n✅ Efficiency Gain:")
old_approach = len(candles) * 5  # 5 features per pair in old approach
new_approach = len(all_features)  # 1 feature per pair
reduction = ((old_approach - new_approach) / old_approach * 100) if old_approach > 0 else 0
print(f"   • Old approach would create: ~{old_approach} documents")
print(f"   • New approach creates: {new_approach} documents")
print(f"   • Reduction: {reduction:.0f}%")

print("=" * 60)

FEATURE ENGINEERING SUMMARY

📊 Data Processing:
   • Pairs processed: 519
   • Features generated: 517 (1 per pair)
   • Signals generated: 73

🎯 Signal Breakdown:
   • Long signals (value > 0): 70
   • Short signals (value < 0): 3
   • Average intensity: 0.795
   • Max intensity: 0.964

💾 Storage:
   • Features saved to MongoDB: 517
   • Signals saved to MongoDB: 73
   • Collection: 'features' and 'signals'

✅ Efficiency Gain:
   • Old approach would create: ~2595 documents
   • New approach creates: 517 documents
   • Reduction: 80%


## Query Stored Features and Signals

Demonstrate retrieving features and signals from storage

## Use Signals for Trading

Now that we have signals, let's prepare them for deployment

In [12]:
# Get top signals for trading
top_long_signals = signals_df[signals_df['direction'] == 'LONG'].head(3)
top_short_signals = signals_df[signals_df['direction'] == 'SHORT'].head(3)

print("🟢 Top 3 Long Signals for Trading:")
display(top_long_signals)

print("\n🔴 Top 3 Short Signals for Trading:")
display(top_short_signals)

# For each signal, we can get the full feature data from storage
if len(top_long_signals) > 0:
    example_pair = top_long_signals.iloc[0]['trading_pair']
    
    # Get the feature to access grid levels
    pair_features = await storage.get_features(
        feature_name="ema_trend",
        trading_pair=example_pair,
        connector_name=CONFIG['connector_name'],
        limit=1
    )
    
    if pair_features:
        feat = pair_features[0]
        range_pct = feat.value['range_pct']
        price = feat.value['price']
        
        print(f"\n💡 Example Grid Levels for {example_pair}:")
        print(f"   Current Price: ${price:.6f}")
        print(f"   Range %: {range_pct*100:.2f}%")
        
        # Calculate grid levels (same logic as before)
        start_price = price * (1 - 0.5 * range_pct)
        end_price = price * (1 + 1.5 * range_pct)
        limit_price = price * (1 - 0.7 * range_pct)
        
        print(f"   Start Price: ${start_price:.6f}")
        print(f"   End Price: ${end_price:.6f}")
        print(f"   Limit Price: ${limit_price:.6f}")

🟢 Top 3 Long Signals for Trading:


trading_pair category  signal_value direction  intensity  range_pct  \
8      SSV-USDT       tf        0.9644      LONG     0.9644 0.15035224   
17    TREE-USDT       tf        0.9428      LONG     0.9428 0.13396005   
68     TIA-USDT       tf        0.9334      LONG     0.9334 0.11537775   

    ema_divergence  
8       0.03250699  
17      0.00069809  
68      0.00778769


🔴 Top 3 Short Signals for Trading:


trading_pair category  signal_value direction  intensity  range_pct  \
19     STO-USDT       tf       -0.7865     SHORT     0.7865 0.15451231   
52     SQD-USDT       tf       -0.7442     SHORT     0.7442 0.14492321   
54     TWT-USDT       tf       -0.7333     SHORT     0.7333 0.11769161   

    ema_divergence  
19     -0.00051963  
52     -0.00194989  
54     -0.00323977


💡 Example Grid Levels for SSV-USDT:
   Current Price: $5.394000
   Range %: 15.04%
   Start Price: $4.988500
   End Price: $6.610500
   Limit Price: $4.826300


In [13]:
# Query recent high-intensity long signals (value > 0.8)
recent_long_signals = await storage.get_signals(
    category='tf',  # trend following
    min_value=0.8,  # Strong long signals
    limit=5
)

print(f"Found {len(recent_long_signals)} high-intensity long signals:")
for sig in recent_long_signals:
    print(f"  {sig.trading_pair}: value={sig.value:.3f} ({sig.signal_name})")

Found 5 high-intensity long signals:
  BEAMX-USDT: value=0.873 (ema_trend_20_200_500)
  XTZ-USDT: value=0.887 (ema_trend_20_200_500)
  MTL-USDT: value=0.837 (ema_trend_20_200_500)
  TIA-USDT: value=0.933 (ema_trend_20_200_500)
  ARB-USDT: value=0.811 (ema_trend_20_200_500)


In [14]:
# Query features for a specific trading pair
example_pair = signals_for_display[0]['trading_pair'] if signals_for_display else "BTC-USDT"

features_for_pair = await storage.get_features(
    feature_name="ema_trend",
    trading_pair=example_pair,
    connector_name=CONFIG['connector_name'],
    limit=1
)

if features_for_pair:
    feat = features_for_pair[0]
    print(f"EMA Trend feature for {example_pair}:")
    print(f"  Timestamp: {feat.timestamp}")
    print(f"\\n  Values:")
    for key, val in feat.value.items():
        if isinstance(val, float):
            print(f"    {key}: {val:.6f}")
        else:
            print(f"    {key}: {val}")
    if feat.info:
        print(f"\\n  Info:")
        for key, val in feat.info.items():
            print(f"    {key}: {val}")
else:
    print(f"No features found for {example_pair}")

EMA Trend feature for STRK-USDT:
  Timestamp: 2025-10-14 16:56:28.184000
\n  Values:
    ema_20: 0.122787
    ema_200: 0.121469
    ema_500: 0.122220
    direction: 1.000000
    intensity: 0.731000
    divergence: 0.000942
    range_pct: 0.120843
    price: 0.123300
\n  Info:
    ema_lengths: [20, 200, 500]
    rolling_window: 1000
    description: EMA trend analysis using [20, 200, 500]
    interval: 1m
